# Install

In [1]:
!apt-get update
!pip install transformers[sentencepiece]
!pip install transformers[torch]
!pip install datasets
!pip install accelerate
!pip install transformers==4.30
!pip install evaluate
!pip install sigopt
!pip install pickle5
!pip install ray[tune]
%env PYTORCH_CUDA_ALLOC_CONF=max_split_size_mb:512

Get:1 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease [3,626 B]
Hit:2 http://archive.ubuntu.com/ubuntu jammy InRelease
Hit:3 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease
Get:4 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [119 kB]
Get:5 http://security.ubuntu.com/ubuntu jammy-security InRelease [110 kB]
Get:6 http://archive.ubuntu.com/ubuntu jammy-backports InRelease [109 kB]
Get:7 http://archive.ubuntu.com/ubuntu jammy-updates/main amd64 Packages [1,235 kB]
Hit:8 https://ppa.launchpadcontent.net/c2d4u.team/c2d4u4.0+/ubuntu jammy InRelease
Get:9 http://archive.ubuntu.com/ubuntu jammy-updates/universe amd64 Packages [1,257 kB]
Get:10 http://security.ubuntu.com/ubuntu jammy-security/universe amd64 Packages [993 kB]
Hit:11 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Get:12 http://security.ubuntu.com/ubuntu jammy-security/main amd64 Packages [966 kB]
Hit:13 https://ppa.launchpadcontent.net/g

# Imports

In [2]:
from transformers import AdamW, AutoTokenizer, AutoModelForSequenceClassification, DataCollatorWithPadding, TrainingArguments, Trainer
import datasets
import torch
import pandas
import numpy as np
import evaluate

# Read and prepare data

In [5]:
dir = '/content/drive/MyDrive/Datasets/' # if you are using something else than collab, change this variable
train_file_name = dir + 'train.csv'
validate_file_name = dir + 'validate.csv'
test_file_name = dir + 'test.csv'

dataset = datasets.load_dataset('csv', data_files={"train": train_file_name, "validation": validate_file_name, "test": test_file_name}, keep_default_na=False)

Extracting data files:   0%|          | 0/3 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

In [6]:
checkpoint = "distilbert-base-uncased"
batch_size = 16
tokenizer = AutoTokenizer.from_pretrained(checkpoint, use_fast=True)

In [7]:
def tokenize_function(example):
    return tokenizer(example["0"], truncation=True)
tokenized_dataset = dataset.map(tokenize_function, batched=True)

Map:   0%|          | 0/621910 [00:00<?, ? examples/s]

Map:   0%|          | 0/207303 [00:00<?, ? examples/s]

Map:   0%|          | 0/207304 [00:00<?, ? examples/s]

In [8]:
tokenized_dataset

DatasetDict({
    train: Dataset({
        features: ['Unnamed: 0', '0', '1', 'input_ids', 'attention_mask'],
        num_rows: 621910
    })
    validation: Dataset({
        features: ['Unnamed: 0', '0', '1', 'input_ids', 'attention_mask'],
        num_rows: 207303
    })
    test: Dataset({
        features: ['Unnamed: 0', '0', '1', 'input_ids', 'attention_mask'],
        num_rows: 207304
    })
})

In [9]:
data_collator = DataCollatorWithPadding(tokenizer=tokenizer)

In [10]:
tokenized_dataset = tokenized_dataset.remove_columns(['Unnamed: 0', '0'])
tokenized_dataset = tokenized_dataset.rename_column('1', 'labels')

# Training (you can skip this stage because I took random parameters just for understanding wheter or not everything is working)

In [ ]:
metric = evaluate.load("accuracy")

def compute_metrics(eval_pred):
  predictions, labels = eval_pred
  predictions = np.argmax(predictions, axis=1)
  return metric.compute(predictions=predictions, references=labels)

model = AutoModelForSequenceClassification.from_pretrained(checkpoint, num_labels=2)

Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_layer_norm.weight', 'vocab_transform.bias', 'vocab_projector.bias', 'vocab_transform.weight', 'vocab_layer_norm.bias']
- This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['pre_classifier.bias', 'pre_classifier.weight', 'classifier.weight', 'classifier.

In [ ]:
training_args = TrainingArguments(
    "some_name",
    evaluation_strategy="epoch",
    save_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=5,
    weight_decay=0.01,
    load_best_model_at_end=True,
    metric_for_best_model='accuracy',
    skip_memory_metrics=True
  )
trainer = Trainer(
    model,
    training_args,
    train_dataset=tokenized_dataset["train"].shard(index=1, num_shards=6000),
    eval_dataset=tokenized_dataset["validation"].shard(index=1, num_shards=6000),
    data_collator=data_collator,
    tokenizer=tokenizer,
    compute_metrics=compute_metrics
)

In [ ]:
trainer.train()

/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
You're using a DistilBertTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=420, training_loss=0.07634077526274181, metrics={'train_runtime': 63.636, 'train_samples_per_second': 104.972, 'train_steps_per_second': 6.6, 'total_flos': 427704113410560.0, 'train_loss': 0.07634077526274181, 'epoch': 5.0})

In [ ]:
trainer.evaluate()

# Hyperparameter search

In [11]:
def model_init():
  return AutoModelForSequenceClassification.from_pretrained(checkpoint, num_labels=2)

metric = evaluate.load("accuracy")

def compute_metrics(eval_pred):
  predictions, labels = eval_pred
  predictions = np.argmax(predictions, axis=-1)
  return metric.compute(predictions=predictions, references=labels)

model = AutoModelForSequenceClassification.from_pretrained(checkpoint, num_labels=2)

searching_args = TrainingArguments(
    "some_name",
    evaluation_strategy="epoch",
    save_strategy="epoch",
    load_best_model_at_end=True,
    skip_memory_metrics=True
  )

scale = 0.02 # Dataset is too big for taking it entirely for hyperparameter search

trainer_search = Trainer(
    model_init=model_init,
    args=searching_args,
    train_dataset=tokenized_dataset["train"].shard(index=1, num_shards=1 / scale),
    eval_dataset=tokenized_dataset["validation"].shard(index=1, num_shards=1 / scale),
    tokenizer=tokenizer
)
trainer_search._memory_tracker.skip_memory_trackers = False

Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_transform.bias', 'vocab_layer_norm.bias', 'vocab_transform.weight', 'vocab_projector.bias', 'vocab_layer_norm.weight']
- This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['pre_classifier.weight', 'classifier.weight', 'pre_classifier.bias', 'classifier.

In [ ]:
# Long part, skip it (4 hours on V100)

def my_hp_space(trial):
    from ray import tune
    return {
        "learning_rate": tune.uniform(1e-5, 5e-5),
        "num_train_epochs": tune.choice(range(1, 6)),
        "per_device_train_batch_size": tune.choice([2,4]),
        "weight_decay": tune.uniform(0.0, 0.3),
        "adam_epsilon": tune.loguniform(1e-10, 1e-6),
        "per_device_eval_batch_size": 32
    }
torch.cuda.empty_cache()
best_run = trainer_search.hyperparameter_search(
    backend="ray",
    n_trials=20,
    hp_space=my_hp_space,
    stop=None,
    checkpoint_score_attr="training_iteration",
    keep_checkpoints_num=0
)

2023-09-11 13:20:16,372	WARNING __init__.py:21 -- Package pickle5 becomes unnecessary in Python 3.8 and above. Its presence may confuse libraries including Ray. Please uninstall the package.
2023-09-11 13:20:18,928	INFO worker.py:1621 -- Started a local Ray instance.
2023-09-11 13:20:21,060	INFO tune.py:226 -- Initializing Ray automatically. For cluster usage or custom Ray initialization, call `ray.init(...)` before `tune.run(...)`.
2023-09-11 13:20:21,083	INFO tune.py:666 -- [output] This will use the new output engine with verbosity 2. To disable the new output and use the legacy output engine, set the environment variable RAY_AIR_NEW_OUTPUT=0. For more information, please see https://github.com/ray-project/ray/issues/36949
/usr/local/lib/python3.10/dist-packages/ray/tune/trainable/function_trainable.py:624: DeprecationWarning: `checkpoint_dir` in `func(config, checkpoint_dir)` is being deprecated. To save and load checkpoint in trainable functions, please use the `ray.air.session` A

+-------------------------------------------------------------------+
| Configuration for experiment     _objective_2023-09-11_13-20-21   |
+-------------------------------------------------------------------+
| Search algorithm                 BasicVariantGenerator            |
| Scheduler                        FIFOScheduler                    |
| Number of trials                 20                               |
+-------------------------------------------------------------------+

View detailed results here: /root/ray_results/_objective_2023-09-11_13-20-21
To visualize your results with TensorBoard, run: `tensorboard --logdir /root/ray_results/_objective_2023-09-11_13-20-21`

Trial status: 16 PENDING
Current time: 2023-09-11 13:20:21. Total running time: 0s
Logical resource usage: 1.0/8 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:V100)
+-------------------------------------------------------------------------------------------------------------------------------------+
| Trial name

(pid=16313) 2023-09-11 13:20:26.383886: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


Trial _objective_f556c_00000 started with configuration:
+------------------------------------------------+
| Trial _objective_f556c_00000 config            |
+------------------------------------------------+
| adam_epsilon                                 0 |
| learning_rate                            2e-05 |
| num_train_epochs                             5 |
| per_device_eval_batch_size                  32 |
| per_device_train_batch_size                  2 |
| weight_decay                            0.2196 |
+------------------------------------------------+



(_objective pid=16313) Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_layer_norm.bias', 'vocab_layer_norm.weight', 'vocab_transform.weight', 'vocab_transform.bias', 'vocab_projector.bias']
(_objective pid=16313) - This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
(_objective pid=16313) - This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
(_objective pid=16313) Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly ini

...

100%|█████████▉| 31097/31100 [14:45<00:00, 35.98it/s]
(_objective pid=49074) 
  0%|          | 0/130 [00:00<?, ?it/s]
(_objective pid=49074) 
  2%|▏         | 2/130 [00:00<00:08, 14.43it/s]
(_objective pid=49074) 
  4%|▍         | 5/130 [00:00<00:06, 20.60it/s]
(_objective pid=49074) 
  6%|▌         | 8/130 [00:00<00:05, 21.29it/s]
(_objective pid=49074) 
  8%|▊         | 11/130 [00:00<00:08, 13.92it/s]
(_objective pid=49074) 
 10%|█         | 13/130 [00:00<00:08, 13.52it/s]
(_objective pid=49074) 
 12%|█▏        | 15/130 [00:01<00:09, 12.37it/s]
(_objective pid=49074) 
 13%|█▎        | 17/130 [00:01<00:09, 11.62it/s]
(_objective pid=49074) 
 15%|█▍        | 19/130 [00:01<00:09, 11.55it/s]
(_objective pid=49074) 
 16%|█▌        | 21/130 [00:01<00:08, 13.07it/s]
(_objective pid=49074) 
 18%|█▊        | 23/130 [00:01<00:08, 11.89it/s]
(_objective pid=49074) 
 19%|█▉        | 25/130 [00:01<00:07, 13.52it/s]
(_objective pid=49074) 
 21%|██        | 27/130 [00:01<00:07, 14.21it/s]
(_objecti

Trial _objective_f556c_00019 finished iteration 5 at 2023-09-11 15:40:44. Total running time: 2hr 20min 23s
+-------------------------------------------------+
| Trial _objective_f556c_00019 result             |
+-------------------------------------------------+
| time_this_iter_s                        177.443 |
| time_total_s                            897.165 |
| training_iteration                            5 |
| epoch                                         5 |
| eval_loss                               0.30379 |
| eval_runtime                              9.551 |
| eval_samples_per_second                 434.196 |
| eval_steps_per_second                    13.611 |
| objective                               0.30379 |
+-------------------------------------------------+

(_objective pid=49074) {'eval_loss': 0.30379343032836914, 'eval_runtime': 9.551, 'eval_samples_per_second': 434.196, 'eval_steps_per_second': 13.611, 'epoch': 5.0}


                                                     
100%|██████████| 130/130 [00:09<00:00, 12.00it/s]
                                                 


Trial _objective_f556c_00019 completed after 5 iterations at 2023-09-11 15:40:46. Total running time: 2hr 20min 25s

Trial status: 20 TERMINATED
Current time: 2023-09-11 15:40:46. Total running time: 2hr 20min 25s
Logical resource usage: 1.0/8 CPUs, 1.0/1 GPUs (0.0/1.0 accelerator_type:V100)
+-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+
| Trial name               status         learning_rate     num_train_epochs     ..._train_batch_size     weight_decay     adam_epsilon     iter     total time (s)     objective     eval_loss     eval_runtime     ...amples_per_second |
+-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+

100%|██████████| 31100/31100 [14:56<00:00, 34.70it/s]


In [ ]:
best_run

BestRun(run_id='f556c_00003', objective=0.18533514440059662, hyperparameters={'learning_rate': 4.754210836063001e-05, 'num_train_epochs': 2, 'per_device_train_batch_size': 4, 'weight_decay': 0.29766346778736524, 'adam_epsilon': 2.9507066707905336e-08, 'per_device_eval_batch_size': 32}, run_summary=<ray.tune.analysis.experiment_analysis.ExperimentAnalysis object at 0x78afd630c790>)

In [12]:
best_run_hyperparameters = {'learning_rate': 4.754210836063001e-05, 'num_train_epochs': 2, 'per_device_train_batch_size': 4, 'weight_decay': 0.29766346778736524, 'adam_epsilon': 2.9507066707905336e-08, 'per_device_eval_batch_size': 32}
for n, v in best_run_hyperparameters.items(): # it should be best_run.hyperparameters but in purpose of skipping search phase I put hyperparameters manually
    setattr(trainer_search.args, n, v)
setattr(trainer_search, 'train_dataset', tokenized_dataset["train"].shard(index=1, num_shards=1 / (10 * scale))) # working with even 20% of dataset takes 30 mins on V100

trainer_search.train()

Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_transform.bias', 'vocab_layer_norm.bias', 'vocab_transform.weight', 'vocab_projector.bias', 'vocab_layer_norm.weight']
- This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['pre_classifier.weight', 'classifier.weight', 'pre_classifier.bias', 'classifier.

TrainOutput(global_step=62192, training_loss=0.14396206925330568, metrics={'train_runtime': 1779.2385, 'train_samples_per_second': 139.815, 'train_steps_per_second': 34.954, 'total_flos': 5517442052384688.0, 'train_loss': 0.14396206925330568, 'epoch': 2.0})

In [13]:
trainer_search.evaluate()

{'eval_loss': 0.11564943939447403,
 'eval_runtime': 9.5508,
 'eval_samples_per_second': 434.202,
 'eval_steps_per_second': 13.611,
 'epoch': 2.0}

# Result on test dataset

In [14]:
metric = evaluate.load("accuracy")

def compute_metrics(eval_pred):
  predictions, labels = eval_pred
  predictions = np.argmax(predictions, axis=1)
  return metric.compute(predictions=predictions, references=labels)

test_dataset = tokenized_dataset["test"].shard(index=1, num_shards=1 / (10 * scale))
predictions = trainer_search.predict(test_dataset)
print(compute_metrics((predictions.predictions, test_dataset['labels'])))

{'accuracy': 0.9777622343889438}


Now using real repository

In [15]:
!pip install pydriller

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.0/66.0 kB 4.1 MB/s eta 0:00:00


I assumed that author is bot if and only if he has 'bot' keyword in his name

In [24]:
from pydriller import Repository

def eval_repo(repo):
  data = []
  for commit in Repository(repo).traverse_commits():
      is_bot = 0
      if commit.author.name.lower().find('bot') >= 0:
        is_bot = 1
      data.append([commit.msg, is_bot])
  df = pandas.DataFrame(data)
  df.to_csv('real_train.csv')
  train_dataset = datasets.load_dataset('csv', data_files='real_train.csv')
  tokenized_train_dataset = train_dataset.map(tokenize_function, batched=True)
  tokenized_train_dataset = tokenized_train_dataset.remove_columns(['Unnamed: 0', '0'])
  tokenized_train_dataset = tokenized_train_dataset.rename_column('1', 'labels')
  metric = evaluate.load("accuracy")

  def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    predictions = np.argmax(predictions, axis=1)
    return metric.compute(predictions=predictions, references=labels)

  predictions = trainer_search.predict(tokenized_train_dataset['train'])
  print(compute_metrics((predictions.predictions, tokenized_train_dataset['train']['labels'])))
  print("Number of bot commits predicted:", np.sum(np.argmax(predictions.predictions, axis=1)))
  print("Number of bot commits in repo:", np.sum(np.array(tokenized_train_dataset['train']['labels'])))
  print("Number of commits in repo:", len(np.array(tokenized_train_dataset['train']['labels'])))

In [21]:
repo1 = 'https://github.com/godotengine/godot'
repo2 = 'https://github.com/halirutan/IntelliJ-Key-Promoter-X'

In [25]:
eval_repo(repo1)

Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Map:   0%|          | 0/57310 [00:00<?, ? examples/s]

{'accuracy': 0.8812074681556448}
Number of bot commits predicted: 6798
Number of bot commits in repo: 14
Number of commits in repo: 57310


In [26]:
eval_repo(repo2)

Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Map:   0%|          | 0/233 [00:00<?, ? examples/s]

{'accuracy': 0.9055793991416309}
Number of bot commits predicted: 22
Number of bot commits in repo: 0
Number of commits in repo: 233
